In [ ]:
import numpy as np
import numpy.random as rdm
from scipy.special import gammainc,gamma,gammaincinv
import astropy.convolution as apcon
import astropy.io.fits as pyfits

In [ ]:
def gen_object(xlims,ylims,maglims,relims,nlims,balims,thetalims):
    "Generate random set of parameters from uniform distribution within intervals"
    x1,x2=xlims
    y1,y2=ylims
    m1,m2=maglims
    r1,r2=relims
    n1,n2=nlims
    b1,b2=balims
    t1,t2=thetalims

    x = rdm.uniform(x1,x2)
    y = rdm.uniform(y1,y2)
    mag = rdm.uniform(m1,m2)
    re = rdm.uniform(r1,r2)
    n = rdm.uniform(n1,n2)
    ba = rdm.uniform(b1,b2)
    theta = rdm.uniform(t1,t2)
    
    return x,y,mag,re,n,ba,theta

In [ ]:
def gammainc(alfa,x):
    return gammainc(alfa,x)*gamma(alfa)

def kappa(n):
    "parameter b in Sersic equation"
    return gammaincinv(2*n,1./2)

def sersic(r,Ie,Re,n):
    "Generic Sersic profile"
    b = kappa(n)
    return Ie*np.exp(-b*(abs(r)/Re)**(1./n)+b)


def get_Ie(re,n,Ftot):
    "Get intensity at re from total flux"
    b = kappa(n)
    return Ftot/(re*re*gamma(2*n)*2*np.pi*n/(b**(2.*n))*np.exp(b))

In [ ]:
def galaxy_maker(imsize,xc,yc,I,r,n,q,theta):
    "create galaxy model image from set of parameters"
    
    X,Y=np.meshgrid(range(imsize[0]),range(imsize[1]))
    ang=np.radians(theta)
    rX=(X-xc)*np.cos(ang)-(Y-yc)*np.sin(ang)
    rY=(X-xc)*np.sin(ang)+(Y-yc)*np.cos(ang)
    R = np.sqrt( rX**2 + (1/q)**2*rY**2 )

    galaxy=sersic(R,I,r,n)
    
    return galaxy

In [ ]:
def create_model_python(path,pars,zp,imsize,convolve=False):
    x,y,m,r,n,q,t=pars

    Ftot = 10**(-0.4*(m-zp))
    Ie = get_Ie(r,n,Ftot)
    
    model_raw = galaxy_maker(imsize,x-1,y-1,Ie,r,n,q,t)

    if convolve:
        model_data = apcon.convolve_fft(model_raw,pyfits.getdata("%s/psf.fits"%path))
    else:
        model_data = model_raw
        
    return model_data

In [ ]:
def add_noise_to_model(model,exptime,gain=1.0,sky_img=None,gauss_sky=[0,1]):
    "Add noise to model. sky_img is either a filename pointing to a sky region or 'gaussian'."
    N,M=model.shape

    if sky_img is None:
        model_wNoise =rdm.poisson(model*exptime*gain)/gain
    elif '.fits' in sky_img:
        sky_back = pyfits.getdata(sky_img)[:N,:M]
        model_wNoise =rdm.poisson(model*exptime*gain)/gain + sky_back*exptime
    elif sky_img == 'gaussian':
        assert len(gauss_sky)==2, 'gauss_sky keyword needs to be a list of 2 parameters: [sky_level,sky_sigma] in cts/second'
        sky_back=rdm.normal(np.zeros(model.shape)+gauss_sky[0]*exptime,gauss_sky[1]*exptime)
        model_wNoise =rdm.poisson(model*exptime*gain)/gain + sky_back
    else:
        raise ValueError('invalid sky_img keyword given: %s'%(sky_img))
    return model_wNoise

In [ ]:
def gaussian(x,a,c,x0,sigma):
    return a*np.exp(-(x-x0)**2/(2*sigma**2))+c

In [ ]:
def create_mock_spectra():
    nwave,ny=1000,50
    canvas = rdm.normal(np.zeros([ny,nwave]))

    for i in range(nwave):
        canvas[:,i] = gaussian(np.arange(ny),rdm.normal(5,3),i/500.,ny/2.,5)

        if rdm.random()>0.99:
            canvas[:,i-1] = gaussian(np.arange(ny),10,i/500.,ny/2.,5)
            canvas[:,i] = gaussian(np.arange(ny),20,i/500.,ny/2.,5)
            canvas[:,i+1] = gaussian(np.arange(ny),10,i/500.,ny/2.,5)

    spec1D = np.sum(canvas[ny/2.-5:ny/2.+5,:],axis=0)
    return spec1D,canvas

In [ ]:
def create_mock_galaxy():
    ImageSize = [200,200]
    Xlims = [75,125]
    Ylims = [75,125]
    MagLims = [18,21]
    ReLims = [10,50]
    Nlims=[0.8,4.5]
    Qlims = [0.15,1.0]
    ThetaLims = [-90,90]

    ZP = 30 ## image zeropoint
    EXPTIME = 1000 ## exposure time in seconds
    parameters = gen_object(Xlims,Ylims,MagLims,ReLims,Nlims,Qlims,ThetaLims)
    gal_model = create_model_python('./',parameters,ZP, ImageSize,convolve=False)
    gal_model_wNoise = add_noise_to_model(gal_model,EXPTIME,sky_img='gaussian',gauss_sky=[0,0.75])
    return gal_model_wNoise

In [ ]:
## An example without any convolution
import matplotlib.pyplot as mpl
    
##    ImageSize = [200,200]
##    Xlims = [75,125]
##    Ylims = [75,125]
##    MagLims = [20,22]
##    ReLims = [10,50]
##    Nlims=[0.8,4.5]
##    Qlims = [0.15,1.0]
##    ThetaLims = [-90,90]
##    parameters = gen_object(Xlims,Ylims,MagLims,ReLims,Nlims,Qlims,ThetaLims)
##
##    ZP = 30 ## image zeropoint
##    EXPTIME = 1000 ## exposure time in seconds
##
##    gal_model = create_model_python('./',parameters,ZP, ImageSize,convolve=False)
##    gal_model_wNoise = add_noise_to_model(gal_model,EXPTIME,sky_img='gaussian',gauss_sky=[0,0.75])
##
##    fig,ax=mpl.subplots(1,2)
##    fig.subplots_adjust(wspace=0)
##
##    ax[0].imshow(gal_model,aspect='equal',vmax=0.5*np.amax(gal_model))
##    ax[1].imshow(gal_model_wNoise,aspect='equal')
##
##    for eixo in ax:
##        eixo.tick_params(labelleft='off',labelbottom='off')
##
##    fig.suptitle(r'$x=%.1f,\ y=%.1f,\ m=%.2f,\ r_e=%.1f,\ n=%.1f,\ q=%.1f,\ \theta=%.1f$'%parameters,fontsize=20)
create_mock_spectra()
mpl.show()